# Описание

- Датасет взят отсюда https://media.xiph.org/video/derf/. Насколько удалось разузнать, в RnD по видеокомпрессии он часто используется для бенчмаркинга алгоритмов. Можем использовать. Внизу есть разные варианты датасетов, для тестов взял objective-1-fast. 

- Данные в raw формате yuv420 (.y4m, в отличии от .yuv, есть хедер с метаданными). Ссылки: https://ru.wikipedia.org/wiki/YUV, 

- Используется opencv-python для загрузки-обработки-сохранения видео.

- В качестве backend-а для i/o используется библиотека ffmpeg. Бинарники для винды лежат в корне проекта. Для Linux-а нужно ставить отдельно.

- На текущий момент не нашел способа сохранять видео обратно в .y4m. Нужно использовать расширение .avi для сохраняемого файла. Иначе все сломается. При этом формат хранения фреймов видео останется прежним. Есть небольшая разница в размерах файла, но она незначительна. Далее будет проверка, что данные, загружаемые из .y4m и .avi одинаковы (одинаковые массивы np.ndarray при выгрузке). Это не всегда выполняется, есть потери. Почему - надо разбираться. В целом, различие минимально, не должно сильно влиять на результат.

Полезные ссылки:
1. https://habr.com/ru/company/erlyvideo/blog/317494/

In [18]:
import matplotlib.pyplot as plt
import numpy as np
import cv2
plt.rcParams['animation.ffmpeg_path'] = r'ffmpeg/bin/ffmpeg.exe'
from matplotlib import animation
from IPython.display import HTML


def play_video(video: np.array, fps: int = 30):
    """
    Plays video specified in np.array
    Input:
    :param: video - np.array [frames, height, width, channels] - RGB uint8
    :param: fps - fps :)
    """
    fig = plt.figure(figsize=(12,6))
    im = plt.imshow(video[0,:,:,:])
    plt.close() # this is required to not display the generated image

    def init():
        im.set_data(video[0,:,:,:])

    def animate(i):
        im.set_data(video[i,:,:,:])
        return im

    anim = animation.FuncAnimation(fig, animate, init_func=init, frames=video.shape[0],
                                   interval=1000.0 / fps)
    return HTML(anim.to_html5_video())

In [2]:
LOAD_FNAME = "data//red_kayak_360p_60f.y4m"
SAVE_FNAME = "data//red_kayak_360p_60f.avi"

### 1. Загрузка видео в массив numpy

In [3]:
from cvtcomp.utils import load_video_to_numpy, save_video_from_numpy

video, fourcc, fps, size = load_video_to_numpy(LOAD_FNAME)

### 2. Модифицирование видео (тест)

In [18]:
modified_video = video.copy() 
modified_video[:,256:768,256:768,:] = 255

 Так можно посмотреть на fourcc исходного видео

In [19]:
import struct

print("FOURCC is '%s'" % struct.pack("<I", int(fourcc)))

FOURCC is 'b'I420''


### Визуализация

In [20]:
%matplotlib inline

play_video(video, fps=20)

In [21]:
modified_video = video.copy() 

modified_video[:,100:200,100:200,:] = 255

play_video(modified_video, fps=20)

### 3. Сохранение видео

In [4]:
save_video_from_numpy(SAVE_FNAME, modified_video, fourcc, fps, size, color=True)

NameError: name 'modified_video' is not defined

### 4. Тесты на потери при загрузки/сохранении

In [5]:
video, fourcc, fps, size = load_video_to_numpy(LOAD_FNAME)
save_video_from_numpy(SAVE_FNAME, video, fourcc, fps, size, color=True)
video_new, _, _, _ = load_video_to_numpy(SAVE_FNAME) 

print(f"RMSE: {(((video_new - video)**2).sum() / video_new.size)**0.5}")

RMSE: 2.279017992095445


In [9]:
print(f"PSNR = {cv2.PSNR(video_new, video)} dB")

video.shape

AttributeError: module 'cv2' has no attribute 'SSIM'

[Wikipedia](https://en.wikipedia.org/wiki/Peak_signal-to-noise_ratio): Typical values for the PSNR in lossy image and video compression are between 30 and 50 dB, provided the bit depth is 8 bits, where higher is better. 

__Вывод:__ Нужно смотреть, из за чего возникают потери (вообще, переход из yuv420 в rgb и обратно может приводить к ним)

In [25]:
play_video(np.abs(video-video_new))

In [26]:
play_video(video)

In [27]:
play_video(video_new)

# New tests

In [20]:
import matplotlib.pyplot as plt
import numpy as np
import cv2
plt.rcParams['animation.ffmpeg_path'] = r'ffmpeg/bin/ffmpeg.exe'
from matplotlib import animation
from IPython.display import HTML

import tensorly as tl

from cvtcomp.base import Encoder, Decoder
from cvtcomp.utils import load_video_to_numpy, save_video_from_numpy, compute_metrics_dataset


encoder = Encoder(encoder_type="tt", quality=0.8)
decoder = Decoder(decoder_type="tt")

In [21]:
LOAD_FNAME = "data//red_kayak_360p_60f.y4m"
video, fourcc, fps, size = load_video_to_numpy(LOAD_FNAME)

video.shape

(60, 360, 640, 3)

In [22]:
compressed_video = encoder.encode(video)

In [23]:
compressed_video[1][0].shape

(360, 288)

In [24]:
decompressed_video = decoder.decode(compressed_video)

In [25]:
cv2.PSNR(video, decompressed_video)

21.29040207546621

In [ ]:
compute_metrics_dataset("data", encoder, decoder, metric="psnr")

 33%|████████████████████████████                                                        | 1/3 [00:05<00:11,  5.98s/it]

In [ ]:
play_video(decompressed_video, fps=20)